In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import gmaps
import os
from census import Census

# Census API Key
# from config import gkey
from config import ckey
url = Census(ckey, year=2018)

In [2]:
# Pulling census data
census_data = url.acs5.get(("NAME", "B19013_001E", "B01003_001E", "B01002_001E",
                          "B19301_001E"), {'for': 'state:*'})

# Convert to DataFrame
census_pd = pd.DataFrame(census_data)

# Column Reordering
census_pd = census_pd.rename(columns={"B01003_001E": "Population",
                                      "B01002_001E": "Median Age",
                                      "B19013_001E": "Household Income",
                                      "B19301_001E": "Per Capita Income",
                                      "NAME": "Name", "state": "State"})

# Final DataFrame
census_pd = census_pd[["State", "Name", "Population", "Median Age", "Household Income",
                       "Per Capita Income"]]

census_pd.head()

State         Name  Population  Median Age  Household Income  \
0    27    Minnesota   5527358.0        37.9           68411.0   
1    28  Mississippi   2988762.0        37.2           43567.0   
2    29     Missouri   6090062.0        38.5           53560.0   
3    30      Montana   1041732.0        39.8           52559.0   
4    31     Nebraska   1904760.0        36.4           59116.0   

   Per Capita Income  
0            36245.0  
1            23434.0  
2            29537.0  
3            29765.0  
4            31101.0

In [3]:
beer_df = pd.read_csv("./output_data/craft_beer_nv.csv")
beer_df.head()

Name    id  Alcohol By Volume  \
0         Possession Porter   723                5.6   
1           Free Bike Amber   742                4.5   
2               Potrero ESB  3982                5.2   
3   Twisted Kilt Scotch Ale  4221                5.0   
4  HarvestÃ¶r Fresh Hop Ale  5243                7.2   

   International Bitterness Units  Standard Reference Method  \
0                               0                          0   
1                               0                          0   
2                               0                          0   
3                               0                          0   
4                               0                          0   

                           Style            Category  \
0                         Porter           Irish Ale   
1   American-Style Amber/Red Ale  North American Ale   
2  Special Bitter or Best Bitter         British Ale   
3                     Scotch Ale         British Ale   
4        American-Style Pale Ale  North American Ale   

                            Brewer           City       State  Latitude  \
0  Diamond Knot Brewery & Alehouse       Mukilteo  Washington   47.9485   
1             Skagit River Brewing   Mount Vernon  Washington   48.4192   
2      21st Amendment Brewery Cafe  San Francisco  California   37.7825   
3              Thirsty Dog Brewing          Akron        Ohio   41.0689   
4              Lift Bridge Brewery     Stillwater   Minnesota   45.0565   

   Longitude   Region  
0  -122.3050     West  
1  -122.3350     West  
2  -122.3930     West  
3   -81.5172  Midwest  
4   -92.8222  Midwest

In [4]:
df = beer_df[['Brewer','City','State','Latitude','Longitude','Region']]
brewery_df = df.drop_duplicates(subset='Brewer', keep='first')
brewery_df

Brewer           City           State  \
0     Diamond Knot Brewery & Alehouse       Mukilteo      Washington   
1                Skagit River Brewing   Mount Vernon      Washington   
2         21st Amendment Brewery Cafe  San Francisco      California   
3                 Thirsty Dog Brewing          Akron            Ohio   
4                 Lift Bridge Brewery     Stillwater       Minnesota   
...                               ...            ...             ...   
1815              Milwaukee Ale House      Milwaukee       Wisconsin   
1839                Titletown Brewing      Green Bay       Wisconsin   
1847             Metropolitan Brewing        Chicago        Illinois   
1880                San Diego Brewing      San Diego      California   
1881        Pinehurst Village Brewery       Aberdeen  North Carolina   

      Latitude  Longitude     Region  
0      47.9485  -122.3050       West  
1      48.4192  -122.3350       West  
2      37.7825  -122.3930       West  
3      41.0689   -81.5172    Midwest  
4      45.0565   -92.8222    Midwest  
...        ...        ...        ...  
1815   43.0334   -87.9093    Midwest  
1839   44.5200   -88.0173    Midwest  
1847   41.9750   -87.6740    Midwest  
1880   32.7922  -117.0990       West  
1881   35.1315   -79.4295  Southeast  

[358 rows x 6 columns]

In [5]:
# Configure gmaps with API key
from config import gkey
gmaps.configure(api_key=gkey)

In [6]:
#Data inputs for Mapping
brew_coord = brewery_df[["Latitude", "Longitude"]]
locations = beer_df[["Latitude", "Longitude"]]
brew_names = brewery_df['Brewer'].to_list()
abv = beer_df['Alcohol By Volume']

In [10]:
# US Brewery Locations Layer
brew_layer = gmaps.symbol_layer(
    brew_coord, hover_text = brew_names, fill_color='rgba(33, 70, 250, 0.4)',
    stroke_color= 'rgba(53, 64, 122, 0.4)', scale=3)


In [11]:
#ABV Heatmap Layer
abv_heat_layer = gmaps.heatmap_layer(locations, weights=abv, 
                                 dissipating=False, max_intensity=100,
                                 point_radius = 1)


abv_heat_layer.gradient = [(255,255,255,0),
                           (20,168,99,1),
                          (231,225,31,0.83),
                          (255,46,0,0.83)]

In [12]:
#Brewery and ABV Map
map_center = (38.4937,-98.3804)
fig = gmaps.figure(center=map_center, zoom_level=4)

fig.add_layer(abv_heat_layer)
fig.add_layer(brew_layer)

fig

Figure(layout=FigureLayout(height='420px'))

In [13]:
centroids = pd.read_csv("./Resources/state_centroids.csv")
center = centroids.sort_values('State', ascending=True)
center.head()

State  Latitude  Longitude
0     Alabama   32.7794   -86.8287
1      Alaska   64.0685  -152.2782
2     Arizona   34.2744  -111.6602
3    Arkansas   34.8938   -92.4426
4  California   37.1841  -119.4696

In [14]:
from collections import Counter

In [15]:
def most_common_style(state):
    state = beer_df.loc[beer_df['State'] == state]
    state_style = state['Style'].to_list()
    words_to_count = (word for word in state_style if word[:1].isupper())
    c = Counter(words_to_count)
    style = c.most_common(3)
    return style

In [16]:
brewer_per_st = brewery_df.groupby(['State']).count()['Brewer']
name = census_pd[['Name']]
st = name.sort_values('Name', ascending=True)
st = st.rename(columns = {"Name":"State"})
st.index = st["State"]
st["Breweries"] = brewer_per_st
st['Breweries'] = st["Breweries"].fillna(0)

In [17]:
abv_group = beer_df.groupby(['State'])
abv_state = abv_group['Alcohol By Volume'].agg([np.mean])
abv_state = round(abv_state,2)
name = census_pd[['Name']]
abv = name.sort_values('Name', ascending=True)
abv = abv.rename(columns = {"Name":"State"})
abv.index = abv["State"]
abv["Alcohol By Vol"] = abv_state
abv["Alcohol By Vol"] = abv["Alcohol By Vol"].fillna(0)

In [20]:
# Interactive US Beer Map
marker_locations = center[["Latitude", "Longitude"]]
brew_list = st['Breweries'].tolist()
abv_list = abv['Alcohol By Vol'].tolist()

state_list = center['State'].to_list()
style_list = []

for state in state_list:
    s = most_common_style(state)
    style_list.append(s)
    
style_list = ['N/A' if x==[] else x for x in style_list]

brewery_info = [
    {'state': state_list[0], 'brew': brew_list[0], 'style': style_list[0], 'abv': abv_list[0]},
    {'state': state_list[1],'brew': brew_list[1], 'style': style_list[1], 'abv': abv_list[1]},
    {'state': state_list[2],'brew': brew_list[2], 'style': style_list[2], 'abv': abv_list[2]},
    {'state': state_list[3],'brew': brew_list[3], 'style': style_list[3], 'abv': abv_list[3]},
    {'state': state_list[4],'brew': brew_list[4], 'style': style_list[4], 'abv': abv_list[4]},
    {'state': state_list[5],'brew': brew_list[5], 'style': style_list[5], 'abv': abv_list[5]},
    {'state': state_list[6],'brew': brew_list[6], 'style': style_list[6], 'abv': abv_list[6]},
    {'state': state_list[7],'brew': brew_list[7], 'style': style_list[7], 'abv': abv_list[7]},
    {'state': state_list[8],'brew': brew_list[8], 'style': style_list[8], 'abv': abv_list[8]},
    {'state': state_list[9],'brew': brew_list[9], 'style': style_list[9], 'abv': abv_list[9]},
    {'state': state_list[10],'brew': brew_list[10], 'style': style_list[10], 'abv': abv_list[10]},
    {'state': state_list[11],'brew': brew_list[11], 'style': style_list[11], 'abv': abv_list[11]},
    {'state': state_list[12],'brew': brew_list[12], 'style': style_list[12], 'abv': abv_list[12]},
    {'state': state_list[13],'brew': brew_list[13], 'style': style_list[13], 'abv': abv_list[13]},
    {'state': state_list[14],'brew': brew_list[14], 'style': style_list[14], 'abv': abv_list[14]},
    {'state': state_list[15],'brew': brew_list[15], 'style': style_list[15], 'abv': abv_list[15]},
    {'state': state_list[16],'brew': brew_list[16], 'style': style_list[16], 'abv': abv_list[16]},
    {'state': state_list[17],'brew': brew_list[17], 'style': style_list[17], 'abv': abv_list[17]},
    {'state': state_list[18],'brew': brew_list[18], 'style': style_list[18], 'abv': abv_list[18]},
    {'state': state_list[19],'brew': brew_list[19], 'style': style_list[19], 'abv': abv_list[19]},
    {'state': state_list[20],'brew': brew_list[20], 'style': style_list[20], 'abv': abv_list[20]},
    {'state': state_list[21],'brew': brew_list[21], 'style': style_list[21], 'abv': abv_list[21]},
    {'state': state_list[22],'brew': brew_list[22], 'style': style_list[22], 'abv': abv_list[22]},
    {'state': state_list[23],'brew': brew_list[23], 'style': style_list[23], 'abv': abv_list[23]},
    {'state': state_list[24],'brew': brew_list[24], 'style': style_list[24], 'abv': abv_list[24]},
    {'state': state_list[25],'brew': brew_list[25], 'style': style_list[25], 'abv': abv_list[25]},
    {'state': state_list[26],'brew': brew_list[26], 'style': style_list[26], 'abv': abv_list[26]},
    {'state': state_list[27],'brew': brew_list[27], 'style': style_list[27], 'abv': abv_list[27]},
    {'state': state_list[28],'brew': brew_list[28], 'style': style_list[28], 'abv': abv_list[28]},
    {'state': state_list[29],'brew': brew_list[29], 'style': style_list[29], 'abv': abv_list[29]},
    {'state': state_list[30],'brew': brew_list[30], 'style': style_list[30], 'abv': abv_list[30]},
    {'state': state_list[31],'brew': brew_list[31], 'style': style_list[31], 'abv': abv_list[31]},
    {'state': state_list[32],'brew': brew_list[32], 'style': style_list[32], 'abv': abv_list[32]},
    {'state': state_list[33],'brew': brew_list[33], 'style': style_list[33], 'abv': abv_list[33]},
    {'state': state_list[34],'brew': brew_list[34], 'style': style_list[34], 'abv': abv_list[34]},
    {'state': state_list[35],'brew': brew_list[35], 'style': style_list[35], 'abv': abv_list[35]},
    {'state': state_list[36],'brew': brew_list[36], 'style': style_list[36], 'abv': abv_list[36]},
    {'state': state_list[37],'brew': brew_list[37], 'style': style_list[37], 'abv': abv_list[37]},
    {'state': state_list[38],'brew': brew_list[38], 'style': style_list[38], 'abv': abv_list[38]},
    {'state': state_list[39],'brew': brew_list[39], 'style': style_list[39], 'abv': abv_list[39]},
    {'state': state_list[40],'brew': brew_list[40], 'style': style_list[40], 'abv': abv_list[40]},
    {'state': state_list[41],'brew': brew_list[41], 'style': style_list[41], 'abv': abv_list[41]},
    {'state': state_list[42],'brew': brew_list[42], 'style': style_list[42], 'abv': abv_list[42]},
    {'state': state_list[43],'brew': brew_list[43], 'style': style_list[43], 'abv': abv_list[43]},
    {'state': state_list[44],'brew': brew_list[44], 'style': style_list[44], 'abv': abv_list[44]},
    {'state': state_list[45],'brew': brew_list[45], 'style': style_list[45], 'abv': abv_list[45]},
    {'state': state_list[46],'brew': brew_list[46], 'style': style_list[46], 'abv': abv_list[46]},
    {'state': state_list[47],'brew': brew_list[47], 'style': style_list[47], 'abv': abv_list[47]},
    {'state': state_list[48],'brew': brew_list[48], 'style': style_list[48], 'abv': abv_list[48]},
    {'state': state_list[49],'brew': brew_list[49], 'style': style_list[49], 'abv': abv_list[49]},
    {'state': state_list[50],'brew': brew_list[50], 'style': style_list[50], 'abv': abv_list[50]},
    {'state': state_list[51],'brew': brew_list[51], 'style': style_list[51], 'abv': abv_list[51]}  
]

info_box_template = """
<dl>
<dt>State</dt><dd>{state}</dd>
<dt>Breweries</dt><dd>{brew}</dd>
<dt>Most Produced Styles</dt><dd>{style}</dd>
<dt>Average ABV</dt><dd>{abv}</dd>
</dl>
"""
beer_info = [info_box_template.format(**brew) for brew in brewery_info]

marker_layer = gmaps.marker_layer(marker_locations, info_box_content=beer_info)

map_center = (38.4937,-98.3804)
fig = gmaps.figure(center=map_center, zoom_level=3.5)
fig.add_layer(marker_layer)
fig

Figure(layout=FigureLayout(height='420px'))